In [25]:
import pycrfsuite
from itertools import chain
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.preprocessing import LabelBinarizer
import sys

In [126]:
train_filename = "data_Train_megam.dat"
test_filename = "data_Train_megam.dat"

In [127]:
train_samples = open(train_filename, "r").read().split("\n")
test_samples = open(test_filename, "r").read().split("\n")

In [128]:
def split_data(word_features):
    X_samples = []
    sample = []
    
    Y_labels = []
    label = []
    
    for word_feature in word_features:
        if word_feature != "":
            word_feature = word_feature.split(" ")
            label.append(word_feature[0])
            sample.append(word_feature[1:])
        else:
            X_samples.append(sample)
            Y_labels.append(label)

            sample = []
            label = []
    return X_samples, Y_labels

In [129]:
%%time 
X_train, Y_train = split_data(train_samples)
X_test, Y_test = split_data(test_samples)

CPU times: user 481 ms, sys: 31.7 ms, total: 512 ms
Wall time: 511 ms


In [130]:
%%time
trainer = pycrfsuite.Trainer(verbose=False)

for xseq, yseq in zip(X_train, Y_train):
    trainer.append(xseq, yseq)

CPU times: user 487 ms, sys: 3.87 ms, total: 491 ms
Wall time: 489 ms


In [131]:
trainer.set_params({
    'c1': 1.0,   # coefficient for L1 penalty
    'c2': 1e-3,  # coefficient for L2 penalty
    'max_iterations': 50,  # stop earlier

    # include transitions that are possible, but not observed
    'feature.possible_transitions': True
})

In [132]:
%%time
trainer.train(train_filename + '_model.crfsuite')

CPU times: user 7.23 s, sys: 0 ns, total: 7.23 s
Wall time: 7.24 s


In [133]:
trainer.logparser.last_iteration


{'active_features': 3504,
 'error_norm': 116.401182,
 'feature_norm': 65.003895,
 'linesearch_step': 1.0,
 'linesearch_trials': 1,
 'loss': 9534.191645,
 'num': 50,
 'scores': {},
 'time': 0.093}

In [134]:
print len(trainer.logparser.iterations), trainer.logparser.iterations[-1]


50 {'loss': 9534.191645, 'error_norm': 116.401182, 'linesearch_trials': 1, 'active_features': 3504, 'num': 50, 'time': 0.093, 'scores': {}, 'linesearch_step': 1.0, 'feature_norm': 65.003895}


In [135]:
tagger = pycrfsuite.Tagger()
tagger.open(train_filename + '_model.crfsuite')

In [136]:

def bio_classification_report(y_true, y_pred):
    """
    Classification report for a list of BIO-encoded sequences.
    It computes token-level metrics and discards "O" labels.
    
    Note that it requires scikit-learn 0.15+ (or a version from github master)
    to calculate averages properly!
    """
    lb = LabelBinarizer()
    y_true_combined = lb.fit_transform(list(chain.from_iterable(y_true)))
    y_pred_combined = lb.transform(list(chain.from_iterable(y_pred)))
        
    tagset = set(lb.classes_) - {'O'}
    tagset = sorted(tagset, key=lambda tag: tag.split('-', 1)[::-1])
    class_indices = {cls: idx for idx, cls in enumerate(lb.classes_)}
    
    return classification_report(
        y_true_combined,
        y_pred_combined,
        labels = [class_indices[cls] for cls in tagset],
        target_names = tagset,
    )

In [137]:
%%time
Y_pred = [tagger.tag(xseq) for xseq in X_test]

CPU times: user 337 ms, sys: 0 ns, total: 337 ms
Wall time: 332 ms


In [138]:
#def output_enti    for x_seq, y_seq in zip(X_train, Y_pred):
for x_seq, y_seq in zip(X_train, Y_pred):
    for word, label in zip(x_seq, y_seq):
        if "drug" in label:
            line = ["drug",]
        print(word, label)

(['form=Increased', 'suf4=ased', 'prev=_BoS_', 'next=nephrotoxicity', 'capitalized'], 'O')
(['form=nephrotoxicity', 'suf4=city', 'prev=Increased', 'next=has'], 'O')
(['form=has', 'suf4=has', 'prev=nephrotoxicity', 'next=been'], 'O')
(['form=been', 'suf4=been', 'prev=has', 'next=reported'], 'O')
(['form=reported', 'suf4=rted', 'prev=been', 'next=following'], 'O')
(['form=following', 'suf4=wing', 'prev=reported', 'next=concomitant'], 'O')
(['form=concomitant', 'suf4=tant', 'prev=following', 'next=administration'], 'O')
(['form=administration', 'suf4=tion', 'prev=concomitant', 'next=of'], 'O')
(['form=of', 'suf4=of', 'prev=administration', 'next=cephalosporins'], 'O')
(['form=cephalosporins', 'suf4=rins', 'prev=of', 'next=and'], 'O')
(['form=and', 'suf4=and', 'prev=cephalosporins', 'next=aminoglycoside'], 'O')
(['form=aminoglycoside', 'suf4=side', 'prev=and', 'next=antibiotics'], 'B-group')
(['form=antibiotics', 'suf4=tics', 'prev=aminoglycoside', 'next=.'], 'I-group')
(['form=.', 'suf4=.

(['form=Transdermal', 'suf4=rmal', 'prev=,', 'next=,', 'capitalized'], 'O')
(['form=,', 'suf4=,', 'prev=Transdermal', 'next=and'], 'O')
(['form=and', 'suf4=and', 'prev=,', 'next=Implantable'], 'O')
(['form=Implantable', 'suf4=able', 'prev=and', 'next=Contraceptives:', 'capitalized'], 'O')
(['form=Contraceptives:', 'suf4=ves:', 'prev=Implantable', 'next=An', 'capitalized'], 'O')
(['form=An', 'suf4=An', 'prev=Contraceptives:', 'next=interaction', 'capitalized'], 'O')
(['form=interaction', 'suf4=tion', 'prev=An', 'next=study'], 'O')
(['form=study', 'suf4=tudy', 'prev=interaction', 'next=demonstrated'], 'O')
(['form=demonstrated', 'suf4=ated', 'prev=study', 'next=that'], 'O')
(['form=that', 'suf4=that', 'prev=demonstrated', 'next=co-administration'], 'O')
(['form=co-administration', 'suf4=tion', 'prev=that', 'next=of'], 'O')
(['form=of', 'suf4=of', 'prev=co-administration', 'next=bosentan'], 'O')
(['form=bosentan', 'suf4=ntan', 'prev=of', 'next=and'], 'O')
(['form=and', 'suf4=and', 'prev=b

(['form=to', 'suf4=to', 'prev=expected', 'next=be'], 'O')
(['form=be', 'suf4=be', 'prev=to', 'next=sensitive'], 'O')
(['form=sensitive', 'suf4=tive', 'prev=be', 'next=to'], 'O')
(['form=to', 'suf4=to', 'prev=sensitive', 'next=alterations'], 'O')
(['form=alterations', 'suf4=ions', 'prev=to', 'next=in'], 'O')
(['form=in', 'suf4=in', 'prev=alterations', 'next=protein'], 'O')
(['form=protein', 'suf4=tein', 'prev=in', 'next=binding'], 'O')
(['form=binding', 'suf4=ding', 'prev=protein', 'next=.'], 'O')
(['form=.', 'suf4=.', 'prev=binding'], 'O')
(['form=Administration', 'suf4=tion', 'prev=_BoS_', 'next=of', 'capitalized'], 'O')
(['form=of', 'suf4=of', 'prev=Administration', 'next=eszopiclone'], 'O')
(['form=eszopiclone', 'suf4=lone', 'prev=of', 'next=3'], 'O')
(['form=3', 'suf4=3', 'prev=eszopiclone', 'next=mg'], 'O')
(['form=mg', 'suf4=mg', 'prev=3', 'next=to'], 'O')
(['form=to', 'suf4=to', 'prev=mg', 'next=a'], 'O')
(['form=a', 'suf4=a', 'prev=to', 'next=patient'], 'O')
(['form=patient', '

(['form=21', 'suf4=21', 'prev=A', 'next=(17)%'], 'O')
(['form=(17)%', 'suf4=17)%', 'prev=21', 'next=decrease'], 'O')
(['form=decrease', 'suf4=ease', 'prev=(17)%', 'next=in'], 'O')
(['form=in', 'suf4=in', 'prev=decrease', 'next=the'], 'O')
(['form=the', 'suf4=the', 'prev=in', 'next=steady-state'], 'O')
(['form=steady-state', 'suf4=tate', 'prev=the', 'next=AUC'], 'O')
(['form=AUC', 'suf4=AUC', 'prev=steady-state', 'next=of', 'capitalized'], 'O')
(['form=of', 'suf4=of', 'prev=AUC', 'next=ganciclovir'], 'O')
(['form=ganciclovir', 'suf4=ovir', 'prev=of', 'next=was'], 'B-drug')
(['form=was', 'suf4=was', 'prev=ganciclovir', 'next=observed'], 'O')
(['form=observed', 'suf4=rved', 'prev=was', 'next=when'], 'O')
(['form=when', 'suf4=when', 'prev=observed', 'next=VIDEX'], 'O')
(['form=VIDEX', 'suf4=IDEX', 'prev=when', 'next=was', 'capitalized'], 'O')
(['form=was', 'suf4=was', 'prev=VIDEX', 'next=administered'], 'O')
(['form=administered', 'suf4=ered', 'prev=was', 'next=2'], 'O')
(['form=2', 'suf4=

(['form=effects', 'suf4=ects', 'prev=the', 'next=of'], 'O')
(['form=of', 'suf4=of', 'prev=effects', 'next=a'], 'O')
(['form=a', 'suf4=a', 'prev=of', 'next=previously'], 'O')
(['form=previously', 'suf4=usly', 'prev=a', 'next=administered'], 'O')
(['form=administered', 'suf4=ered', 'prev=previously', 'next=botulinum'], 'O')
(['form=botulinum', 'suf4=inum', 'prev=administered', 'next=toxin'], 'B-group')
(['form=toxin', 'suf4=oxin', 'prev=botulinum', 'next=.'], 'I-group')
(['form=.', 'suf4=.', 'prev=toxin'], 'O')
(['form=Phenothiazines', 'suf4=ines', 'prev=_BoS_', 'next=-', 'capitalized'], 'O')
(['form=-', 'suf4=-', 'prev=Phenothiazines', 'next=Taking'], 'O')
(['form=Taking', 'suf4=king', 'prev=-', 'next=piperazine', 'capitalized'], 'O')
(['form=piperazine', 'suf4=zine', 'prev=Taking', 'next=and'], 'O')
(['form=and', 'suf4=and', 'prev=piperazine', 'next=a'], 'O')
(['form=a', 'suf4=a', 'prev=and', 'next=phenothiazine'], 'O')
(['form=phenothiazine', 'suf4=zine', 'prev=a', 'next=together'], '

...

(['form=gain', 'suf4=gain', 'prev=bodyweight', 'next=and'], 'O')
(['form=and', 'suf4=and', 'prev=gain', 'next=increased'], 'O')
(['form=increased', 'suf4=ased', 'prev=and', 'next=appetite'], 'O')
(['form=appetite', 'suf4=tite', 'prev=increased', 'next=and'], 'O')
(['form=and', 'suf4=and', 'prev=appetite', 'next=compared'], 'O')
(['form=compared', 'suf4=ared', 'prev=and', 'next=with'], 'O')
(['form=with', 'suf4=with', 'prev=compared', 'next=risperidone'], 'O')
(['form=risperidone', 'suf4=done', 'prev=with', 'next=,'], 'O')
(['form=,', 'suf4=,', 'prev=risperidone', 'next=only'], 'O')
(['form=only', 'suf4=only', 'prev=,', 'next=bodyweight'], 'O')
(['form=bodyweight', 'suf4=ight', 'prev=only', 'next=gain'], 'O')
(['form=gain', 'suf4=gain', 'prev=bodyweight', 'next=occurred'], 'O')
(['form=occurred', 'suf4=rred', 'prev=gain', 'next=significantly'], 'O')
(['form=significantly', 'suf4=ntly', 'prev=occurred', 'next=more'], 'O')
(['form=more', 'suf4=more', 'prev=significantly', 'next=frequently

(['form=The', 'suf4=The', 'prev=_BoS_', 'next=clinical', 'capitalized'], 'O')
(['form=clinical', 'suf4=ical', 'prev=The', 'next=significance'], 'O')
(['form=significance', 'suf4=ance', 'prev=clinical', 'next=of'], 'O')
(['form=of', 'suf4=of', 'prev=significance', 'next=this'], 'O')
(['form=this', 'suf4=this', 'prev=of', 'next=observation'], 'O')
(['form=observation', 'suf4=tion', 'prev=this', 'next=is'], 'O')
(['form=is', 'suf4=is', 'prev=observation', 'next=unknown'], 'O')
(['form=unknown', 'suf4=nown', 'prev=is', 'next=.'], 'O')
(['form=.', 'suf4=.', 'prev=unknown'], 'O')
(['form=FLUOTHANE', 'suf4=HANE', 'prev=_BoS_', 'next=augments', 'capitalized'], 'O')
(['form=augments', 'suf4=ents', 'prev=FLUOTHANE', 'next=the'], 'O')
(['form=the', 'suf4=the', 'prev=augments', 'next=action'], 'O')
(['form=action', 'suf4=tion', 'prev=the', 'next=of'], 'O')
(['form=of', 'suf4=of', 'prev=action', 'next=non-depolarising'], 'O')
(['form=non-depolarising', 'suf4=sing', 'prev=of', 'next=muscle'], 'O')
(

(['form=barbiturates', 'suf4=ates', 'prev=,', 'next=,'], 'O')
(['form=,', 'suf4=,', 'prev=barbiturates', 'next=tranquilizers'], 'O')
(['form=tranquilizers', 'suf4=zers', 'prev=,', 'next=,'], 'O')
(['form=,', 'suf4=,', 'prev=tranquilizers', 'next=and'], 'O')
(['form=and', 'suf4=and', 'prev=,', 'next=antihistamines)'], 'O')
(['form=antihistamines)', 'suf4=nes)', 'prev=and', 'next=may'], 'O')
(['form=may', 'suf4=may', 'prev=antihistamines)', 'next=result'], 'O')
(['form=result', 'suf4=sult', 'prev=may', 'next=in'], 'O')
(['form=in', 'suf4=in', 'prev=result', 'next=increased'], 'O')
(['form=increased', 'suf4=ased', 'prev=in', 'next=central'], 'O')
(['form=central', 'suf4=tral', 'prev=increased', 'next=nervous'], 'O')
(['form=nervous', 'suf4=vous', 'prev=central', 'next=system'], 'O')
(['form=system', 'suf4=stem', 'prev=nervous', 'next=depressant'], 'O')
(['form=depressant', 'suf4=sant', 'prev=system', 'next=effects'], 'O')
(['form=effects', 'suf4=ects', 'prev=depressant', 'next=.'], 'O')
(

(['form=with', 'suf4=with', 'prev=together', 'next=penicillamine'], 'O')
(['form=penicillamine', 'suf4=mine', 'prev=with', 'next=(Depen'], 'O')
(['form=(Depen', 'suf4=epen', 'prev=penicillamine', 'next=,'], 'O')
(['form=,', 'suf4=,', 'prev=(Depen', 'next=Cuprimine)'], 'O')
(['form=Cuprimine)', 'suf4=ine)', 'prev=,', 'next=,', 'capitalized'], 'O')
(['form=,', 'suf4=,', 'prev=Cuprimine)', 'next=another'], 'O')
(['form=another', 'suf4=ther', 'prev=,', 'next=arthritis'], 'O')
(['form=arthritis', 'suf4=itis', 'prev=another', 'next=medication'], 'O')
(['form=medication', 'suf4=tion', 'prev=arthritis', 'next=.'], 'O')
(['form=.', 'suf4=.', 'prev=medication'], 'O')
(['form=It', 'suf4=It', 'prev=_BoS_', 'next=should', 'capitalized'], 'O')
(['form=should', 'suf4=ould', 'prev=It', 'next=also'], 'O')
(['form=also', 'suf4=also', 'prev=should', 'next=be'], 'O')
(['form=be', 'suf4=be', 'prev=also', 'next=avoided'], 'O')
(['form=avoided', 'suf4=ided', 'prev=be', 'next=in'], 'O')
(['form=in', 'suf4=in'

(['form=,', 'suf4=,', 'prev=carbamazepine', 'next=cimetidine'], 'O')
(['form=cimetidine', 'suf4=dine', 'prev=,', 'next=,'], 'O')
(['form=,', 'suf4=,', 'prev=cimetidine', 'next=ketoconazole)'], 'O')
(['form=ketoconazole)', 'suf4=ole)', 'prev=,', 'next=,'], 'O')
(['form=,', 'suf4=,', 'prev=ketoconazole)', 'next=though'], 'O')
(['form=though', 'suf4=ough', 'prev=,', 'next=this'], 'O')
(['form=this', 'suf4=this', 'prev=though', 'next=has'], 'O')
(['form=has', 'suf4=has', 'prev=this', 'next=not'], 'O')
(['form=not', 'suf4=not', 'prev=has', 'next=been'], 'O')
(['form=been', 'suf4=been', 'prev=not', 'next=studied'], 'O')
(['form=studied', 'suf4=died', 'prev=been'], 'O')
(['form=.', 'suf4=.', 'prev=_BoS_'], 'O')
(['form=Since', 'suf4=ince', 'prev=_BoS_', 'next=Zarontin', 'capitalized'], 'O')
(['form=Zarontin', 'suf4=ntin', 'prev=Since', 'next=(ethosuximide)', 'capitalized'], 'O')
(['form=(ethosuximide)', 'suf4=ide)', 'prev=Zarontin', 'next=may'], 'O')
(['form=may', 'suf4=may', 'prev=(ethosuxim

In [143]:
"HOLA".istitle()

False

In [139]:
def output_predicted_entities(Y_pred):
    Y_pred_flatten = [el for line in Y_pred for el in line]
    detailed_word_features = open("data_Train_feats.dat").read().split("\n")
    detailed_word_features = [el for el in detailed_word_features if el != ""]
    
    for label, word_feature in zip(Y_pred_flatten,detailed_word_features):
        if label == "O":
            continue
        else:
            label = label.split("-")[1]
            _id, word, offset_from, offset_to = word_feature.split(" ")[:4]
            line = [_id, "{}-{}".format(offset_from, offset_to), word, label]
            outputfile.write("|".join(line) + "\n")


In [140]:
outputfile = open("hola.txt", "w")
output_predicted_entities(Y_pred)
outputfile.close()

In [141]:
print(bio_classification_report(Y_test, Y_pred))


              precision    recall  f1-score   support

     B-brand       0.83      0.57      0.68       473
     I-brand       1.00      0.47      0.64        17
      B-drug       0.81      0.61      0.70      2854
      I-drug       0.79      0.48      0.59       174
    B-drug_n       0.85      0.42      0.56       159
    I-drug_n       0.64      0.25      0.36        28
     B-group       0.85      0.54      0.66       929
     I-group       0.85      0.57      0.68       603

   micro avg       0.82      0.58      0.68      5237
   macro avg       0.83      0.49      0.61      5237
weighted avg       0.82      0.58      0.68      5237
 samples avg       0.02      0.02      0.02      5237



In [142]:
from collections import Counter
info = tagger.info()

def print_transitions(trans_features):
    for (label_from, label_to), weight in trans_features:
        print("%-6s -> %-7s %0.6f" % (label_from, label_to, weight))

print("Top likely transitions:")
print_transitions(Counter(info.transitions).most_common(15))

print("\nTop unlikely transitions:")
print_transitions(Counter(info.transitions).most_common()[-15:])

Top likely transitions:
O      -> O       6.306696
B-group -> I-group 5.584653
B-drug_n -> I-drug_n 5.041959
I-group -> I-group 4.873304
I-drug_n -> I-drug_n 4.130055
B-drug -> I-drug  3.704736
B-brand -> I-brand 3.327522
O      -> B-drug  3.271012
I-drug -> I-drug  3.037962
B-drug -> O       2.737865
B-group -> O       2.628012
B-drug_n -> O       2.242394
B-brand -> O       2.182316
O      -> B-group 2.092251
I-group -> O       1.982841

Top unlikely transitions:
B-drug_n -> B-brand -0.717688
I-drug -> B-brand -0.756350
I-brand -> B-brand -0.808869
I-group -> B-brand -0.895362
B-group -> B-group -0.965026
O      -> I-drug  -0.986978
B-group -> B-brand -1.223175
B-brand -> B-group -1.403115
O      -> I-brand -1.443811
B-drug -> I-group -1.447992
B-drug -> B-drug  -1.764949
B-drug -> B-group -1.980907
O      -> I-group -2.401827
B-brand -> B-brand -2.716318
B-drug -> B-brand -2.795083
